In [119]:
import pandas as pd
import numpy as np
from keras.preprocessing.text import Tokenizer
import regex as re

In [120]:
data=pd.read_csv('bbc-news-data.csv', sep='\t')

In [121]:
data

category filename                              title  \
0     business  001.txt  Ad sales boost Time Warner profit   
1     business  002.txt   Dollar gains on Greenspan speech   
2     business  003.txt  Yukos unit buyer faces loan claim   
3     business  004.txt  High fuel prices hit BA's profits   
4     business  005.txt  Pernod takeover talk lifts Domecq   
...        ...      ...                                ...   
2220      tech  397.txt   BT program to beat dialler scams   
2221      tech  398.txt    Spam e-mails tempt net shoppers   
2222      tech  399.txt            Be careful how you code   
2223      tech  400.txt    US cyber security chief resigns   
2224      tech  401.txt   Losing yourself in online gaming   

                                                content  
0      Quarterly profits at US media giant TimeWarne...  
1      The dollar has hit its highest level against ...  
2      The owners of embattled Russian oil giant Yuk...  
3      British Airways has blamed high fuel prices f...  
4      Shares in UK drinks and food firm Allied Dome...  
...                                                 ...  
2220   BT is introducing two initiatives to help bea...  
2221   Computer users across the world continue to i...  
2222   A new European directive could put software w...  
2223   The man making sure US computer networks are ...  
2224   Online role playing games are time-consuming,...  

[2225 rows x 4 columns]

In [122]:
content=list(data.content.values)

In [123]:
corpus="\n".join(content)

In [124]:
corpus=corpus.lower()

In [125]:
corpus = re.sub('[^\w\s]','', corpus )

In [126]:
t=Tokenizer(num_words=None)


In [127]:
corpus=corpus[:100000]

In [128]:
t.fit_on_texts([corpus])

In [129]:
input_sequences = []
for sentence in corpus.split('\n'):
  print(sentence)
  tokenized_sentence = t.texts_to_sequences([sentence])[0]
  print(tokenized_sentence)
  for i in range(1,len(tokenized_sentence)):
    input_sequences.append(tokenized_sentence[:i+1])

 quarterly profits at us media giant timewarner jumped 76 to 113bn 600m for the three months to december from 639m yearearlier  the firm which is now one of the biggest investors in google benefited from sales of highspeed internet connections and higher advert sales timewarner said fourth quarter sales rose 2 to 111bn from 109bn its profits were buoyed by oneoff gains which offset a profit dip at warner bros and less users for aol  time warner said on friday that it now owns 8 of searchengine google but its own internet business aol had has mixed fortunes it lost 464000 subscribers in the fourth quarter profits were lower than in the preceding three quarters however the company said aols underlying profit before exceptional items rose 8 on the back of stronger internet advertising revenues it hopes to increase subscribers by offering the online service free to timewarner internet customers and will try to sign up aols existing customers for highspeed broadband timewarner also has to r

In [130]:
input_sequences

[[501, 78],
 [501, 78, 21],
 [501, 78, 21, 26],
 [501, 78, 21, 26, 347],
 [501, 78, 21, 26, 347, 259],
 [501, 78, 21, 26, 347, 259, 348],
 [501, 78, 21, 26, 347, 259, 348, 1056],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2, 1659],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2, 1659, 1660],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2, 1659, 1660, 7],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2, 1659, 1660, 7, 1],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2, 1659, 1660, 7, 1, 92],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2, 1659, 1660, 7, 1, 92, 111],
 [501, 78, 21, 26, 347, 259, 348, 1056, 1658, 2, 1659, 1660, 7, 1, 92, 111, 2],
 [501,
  78,
  21,
  26,
  347,
  259,
  348,
  1056,
  1658,
  2,
  1659,
  1660,
  7,
  1,
  92,
  111,
  2,
  206],
 [501,
  78,
  21,
  26,
  347,
  259,
  348,
  1056,
  1658,
  2,
  1659,
  1660,
  7,
  1,
  92,
  111,
  2,
  206,
  19],


In [131]:
word2ind=t.word_index

In [132]:
max_len = max([len(x) for x in input_sequences])

In [133]:
from tensorflow.keras.preprocessing.sequence import pad_sequences
padded_input_sequences = pad_sequences(input_sequences, maxlen = max_len, padding='pre')

In [134]:
X = padded_input_sequences[:,:-1]
Y = padded_input_sequences[:,-1]

In [135]:
Y.shape

(16937,)

In [136]:
len(word2ind)

3759

In [137]:
X.shape

(16937, 642)

In [138]:
from tensorflow.keras.utils import to_categorical
Y = to_categorical(Y,num_classes=max(Y)+1)

In [139]:
Y.shape

(16937, 3760)

In [140]:
##Model Generation

In [141]:
from keras.models import Sequential

In [142]:
from keras.layers import Dense,LSTM,Embedding
from tensorflow.keras.losses import CategoricalCrossentropy
from tensorflow.keras.optimizers import Adam


In [143]:
model = Sequential()
model.add(Embedding(3760, 100, input_length=642))
model.add(LSTM(150))
model.add(Dense(3760, activation='softmax'))

In [144]:
model.compile(optimizer=Adam(learning_rate=0.001),
              loss= CategoricalCrossentropy(),
              metrics=['accuracy'],run_eagerly=True)

In [145]:
Y.shape

(16937, 3760)

In [146]:
model.fit(X,Y,batch_size=32, epochs=30,validation_split=0.2)

Epoch 1/30
424/424 [==============================] - 89s 208ms/step - loss: 7.1102 - accuracy: 0.0609 - val_loss: 7.0654 - val_accuracy: 0.0649
Epoch 2/30
424/424 [==============================] - 59s 139ms/step - loss: 6.6307 - accuracy: 0.0637 - val_loss: 7.2185 - val_accuracy: 0.0714
Epoch 3/30
424/424 [==============================] - 46s 107ms/step - loss: 6.4438 - accuracy: 0.0737 - val_loss: 7.2672 - val_accuracy: 0.0812
Epoch 4/30
424/424 [==============================] - 41s 96ms/step - loss: 6.2227 - accuracy: 0.0879 - val_loss: 7.2515 - val_accuracy: 0.0835
Epoch 5/30
424/424 [==============================] - 37s 87ms/step - loss: 5.9633 - accuracy: 0.0972 - val_loss: 7.3554 - val_accuracy: 0.0865
Epoch 6/30
424/424 [==============================] - 37s 87ms/step - loss: 5.6635 - accuracy: 0.1110 - val_loss: 7.4149 - val_accuracy: 0.0921
Epoch 7/30
424/424 [==============================] - 33s 78ms/step - loss: 5.3489 - accuracy: 0.1267 - val_loss: 7.5238 - val_accura

In [147]:
model.summary()

Model: "sequential_4"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_4 (Embedding)     (None, 642, 100)          376000    
                                                                 
 lstm_4 (LSTM)               (None, 150)               150600    
                                                                 
 dense_4 (Dense)             (None, 3760)              567760    
                                                                 
Total params: 1094360 (4.17 MB)
Trainable params: 1094360 (4.17 MB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [153]:
text="I hope this"
for i in range(20):
  text_sequence=t.texts_to_sequences([text])[0]
  padded_text = pad_sequences([text_sequence], maxlen=642)
  xt=model.predict(padded_text)
  x=np.argmax(xt)
  for word,index in word2ind.items():
    if(index==x):
      text = text + " " +str(word)
print(text)


1/1 [==============================] - 0s 33ms/step
I hope this giant has to be held by oneoff three months would cut its media and corporate giant has said the netherlandsbased


In [154]:
model_json = model.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)
model.save_weights("model.h5")